## Visualizing ICESat-2 Data
### Elevation Visualization Example Notebook

This notebook demonstrates interactive ICESat-2 elevation data visualization by requesting data directly from [OpenAltimetry](https://www.openaltimetry.org/) based on metadata provided by [icepyx](https://icepyx.readthedocs.io/en/latest/). We will show how to plot spatial extent and elevation ditributions interactively. 

#### Credits
* Notebook by: [Tian Li (University of Bristol)](https://github.com/icetianli)
* Source material: [ICESat-2 Geohackweek READ_ATL06_DEM Notebook](https://github.com/ICESAT-2HackWeek/Assimilation/blob/master/contributors/icetianli/READ_ATL06_DEM.ipynb) by Tian Li and [Friedrich Knuth (University of Washington)](https://github.com/friedrichknuth)

### Import packages

In [ ]:
import icepyx as ipx
from icepyx.core.visualization import Visualize

### Create an ICESat-2 data object
Set desired parameters for data query, including `short_name`, `date_range` and `spatial_extent`, for details please refer to [ICESat-2_DAAC_DataAccess_Example](https://github.com/icesat2py/icepyx/blob/development/examples/ICESat-2_DAAC_DataAccess_Example.ipynb).

In [3]:
#bounding box
# Larsen C Ice Shelf
short_name = 'ATL06'
date_range = ['2019-5-25', '2019-8-1']
spatial_extent = [-67, -70, -59, -65] 

In [4]:
# https://nsidc.org/data/ATL07/versions/2
# short_name = 'ATL07'
# date_range = ['2019-5-25', '2019-8-1']
# spatial_extent = [-28, 82, -25, 84]

In [5]:
# #polygon vertices
# short_name = 'ATL06'
# date_range = ['2019-02-20','2019-02-28']
# spatial_extent = [(-55, 68), (-55, 71), (-48, 71), (-48, 68), (-55, 68)]

In [6]:
# #polygon geospatial file
# short_name = 'ATL06'
# date_range = ['2019-10-01','2019-10-05']
# spatial_extent = './supporting_files/data-access_PineIsland/glims_polygons.shp'

Create an ICESat-2 data object based on query parameters 

In [7]:
region = ipx.Query(short_name, spatial_extent, date_range)
print(region.dataset)
print(region.dates)
print(region.start_time)
print(region.end_time)
print(region.dataset_version)
print(region.cycles)
print(region.tracks)

ATL06
['2019-05-25', '2019-08-01']
00:00:00
23:59:59
003
['03', '04']
['0186', '0201', '0239', '0247', '0262', '0300', '0308', '0315', '0323', '0361', '0369', '0376', '0384', '0422', '0430', '0437', '0445', '0483', '0498', '0506', '0872', '0879', '0887', '0925', '0933', '0940', '0948', '0986', '1001', '1009', '1047', '1062', '1070', '1085', '1123', '1131', '1184', '1192', '1207', '1245', '1253', '1260', '1268', '1306', '1314', '1321', '1329']


### Visualize spatial extent 
To use visualization module, we need to create a Visualize object first. By calling function `visualize_extent`, it will plot the spatial extent in red outline overlaid on a basemap, try zoom-in/zoom-out to see where is your interested region and what the geographic features look like in this region.

In [8]:
region_viz = Visualize(short_name, spatial_extent, date_range)
region_viz.visualize_extent()

:Overlay
   .WMTS.I :WMTS   [Longitude,Latitude]
   .Path.I :Path   [Longitude,Latitude]

### Visualize ICESat-2 surface elevation distribution using OpenAltimetry API

#### ***Note: this function currently only supports products [ATL06, ATL07, ATL08, ATL10, ATL12, ATL13] and bounding_box query object***

Now we have produced an interactive map showing the spatial extent of ICESat-2 data to be requested from icepyx, what if we want to quickly check the elevation distribution of ICESat-2 data we plan to download from NSIDC? [OpenAltimetry API](https://openaltimetry.org/data/swagger-ui/#/) provides a nice way to achieve this. By sending metadata (product, date, bounding box, trackId) of each ICESat-2 file to API, it can return elevation data instantaneously. The major drawback is requests are limited to 5x5 degree spatial bounding box selection for most of the ICESat-2 L3A products [ATL06, ATL07, ATL08, ATL10, ATL12, ATL13](https://icesat-2.gsfc.nasa.gov/science/data-products). To get around this issue, the input spatial extent will be splited into 5x5 degree lat/lon grid first, then use icepyx to query metadata of ICESat-2 files located in each grid, iterate through list of metadata of each grid and send request to OpenAltimetry. 

#### Plot elevation from the lastest cycle 

In [9]:
cyclemap, rgtmap, OA_ds = region_viz.visualize_elevation()
cyclemap

Generating urls
Sending request to OpenAltimetry, please wait...


100%|██████████| 24/24 [06:45<00:00, 16.89s/it]


Plot elevation, please wait...


:DynamicMap   [cycle]
   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Image.I :Image   [x,y]   (x_y elevation)

#### Plot elevation for individual RGT

In [10]:
rgtmap

:Layout
   .DynamicMap.I  :DynamicMap   [rgt]
      :Overlay
         .Tiles.I :Tiles   [x,y]
         .Image.I :Image   [x,y]   (x_y elevation)
   .DynamicMap.II :DynamicMap   [rgt]
      :Image   [lat,elevation]   (lat_elevation elevation)

#### Check requested elevation data 
The requested elevation data from OpenAltimetry are organized in a xarray dataset

In [11]:
# write data into netcdf
OA_ds.to_netcdf('./ATL06_OA_Elev.nc')
OA_ds

<xarray.Dataset>
Dimensions:    (bbox: 2, cycle: 1, index: 8445, rgt: 19)
Coordinates:
  * bbox       (bbox) <U20 '[-62, -70, -59, -65]' '[-67, -70, -62, -65]'
  * index      (index) int64 0 1 2 3 4 5 6 ... 8439 8440 8441 8442 8443 8444
  * rgt        (rgt) int64 186 201 239 247 262 300 ... 430 437 445 483 498 506
  * cycle      (cycle) int64 4
Data variables:
    elevation  (rgt, cycle, bbox, index) float64 dask.array<chunksize=(19, 1, 2, 1000), meta=np.ndarray>
    lat        (rgt, cycle, bbox, index) float64 dask.array<chunksize=(19, 1, 2, 1000), meta=np.ndarray>
    lon        (rgt, cycle, bbox, index) float64 dask.array<chunksize=(19, 1, 2, 1000), meta=np.ndarray>

### Move on to data downloading from NSIDC if these are the datasets of interest

In [ ]:
earthdata_uid = 'yourearthdataid'
email = 'youremailaddress'
region.earthdata_login(earthdata_uid, email)
region.order_granules()

#view a short list of order IDs
region.granules.orderIDs

path = 'your data directory'
region.download_granules(path)